In [1]:
import json
import os

import numpy as np
import torch
from torch import nn


def read_data(train_data_dir, test_data_dir):
    '''parses data in given train and test data directories

    assumes:
    - the data in the input directories are .json files with 
        keys 'users' and 'user_data'
    - the set of train set users is the same as the set of test set users

    Return:
        clients: list of client ids
        groups: list of group ids; empty list if none found
        train_data: dictionary of train data
        test_data: dictionary of test data
    '''
    clients = []
    groups = []
    train_data = {}
    test_data = {}

    train_files = os.listdir(train_data_dir)
    train_files = [f for f in train_files if f.endswith('.json')]
    for f in train_files:
        file_path = os.path.join(train_data_dir, f)
        with open(file_path, 'r') as inf:
            cdata = json.load(inf)
        clients.extend(cdata['users'])
        if 'hierarchies' in cdata:
            groups.extend(cdata['hierarchies'])
        train_data.update(cdata['user_data'])

    test_files = os.listdir(test_data_dir)
    test_files = [f for f in test_files if f.endswith('.json')]
    for f in test_files:
        file_path = os.path.join(test_data_dir, f)
        with open(file_path, 'r') as inf:
            cdata = json.load(inf)
        test_data.update(cdata['user_data'])

    #clients = list(sorted(train_data.keys()))

    return clients, groups, train_data, test_data

In [2]:
ALL_LETTERS = "\n !\"&'(),-.0123456789:;>?ABCDEFGHIJKLMNOPQRSTUVWXYZ[]abcdefghijklmnopqrstuvwxyz}"
NUM_LETTERS = len(ALL_LETTERS)

def _one_hot(index, size):
    '''returns one-hot vector with given size and value 1 at given index
    '''
    vec = [0 for _ in range(size)]
    vec[int(index)] = 1
    return vec


def letter_to_vec(letter):
    '''returns one-hot representation of given letter
    '''
    index = ALL_LETTERS.find(letter)
    #print("START",letter,"END", index)
    return _one_hot(index, NUM_LETTERS)


def word_to_indices(word):
    '''returns a list of character indices
    Args:
        word: string

    Return:
        indices: int list with length len(word)
    '''
    indices = []
    for c in word:
        indices.append(ALL_LETTERS.find(c))
    return indices

In [3]:
def process_x(raw_x_batch):
        x_batch = [word_to_indices(word) for word in raw_x_batch]
        x_batch = np.array(x_batch)
        x_batch = torch.from_numpy(x_batch)
        return x_batch

def process_y(raw_y_batch):
    y_batch = [word_to_indices(word) for word in raw_y_batch]
    #print("HO: ", len(y_batch), len(y_batch[0]))
    #print(len(y_batch), y_batch[0])
    y_batch = torch.tensor(y_batch)
    return y_batch

def batch_data(data, batch_size, seed):
    '''
    data is a dict := {'x': [numpy array], 'y': [numpy array]} (on one client)
    returns x, y, which are both numpy array of length: batch_size
    '''
    data_x = data['x']
    data_y = data['y']
    # randomly shuffle data
    np.random.seed(seed)
    rng_state = np.random.get_state()
    np.random.shuffle(data_x)
    np.random.set_state(rng_state)
    np.random.shuffle(data_y)
    batches = []
    # loop through mini-batches
    for i in range(0, len(data_x), batch_size):
        batched_x = process_x(data_x[i:i+batch_size])
        batched_y = process_y(data_y[i:i+batch_size])
        batches.append((batched_x, batched_y))
    return batches

In [4]:
train_path = "data/shakespeare/train"
test_path = "data/shakespeare/test"
users, groups, train_data, test_data = read_data(train_path, test_path)

In [5]:
sentence_len = None
test_data_local_dict = dict()
client_num = 0
for u, g in zip(users, groups):
    #Train data
    #print("Group: ", g)
    #print("User: ", u)
    for ind, (sentence_slice, next_letter) in enumerate(zip(train_data[u]['x'], train_data[u]['y'])):
        #print(len(sentence_slice))
        if sentence_len is None:
            sentence_len = len(sentence_slice)
        else:
            assert sentence_len == len(sentence_slice), "inconsistent sentence length in train dataset!"
        train_data[u]['y'][ind] = (sentence_slice[1:]+next_letter)
        #print(sentence_slice, " --> ", (sentence_slice[1:]+next_letter))
    
    #Test data
    for ind, (sentence_slice, next_letter) in enumerate(zip(test_data[u]['x'], test_data[u]['y'])):
        #print(len(sentence_slice))
        if sentence_len is None:
            sentence_len = len(sentence_slice)
        else:
            assert sentence_len == len(sentence_slice), "inconsistent sentence length in test dataset!"
            #assert (sentence_len!=len(sentence_slice) and isinstance(sentence_len, int)), "Inconsistent sentence length!!!"
        test_data[u]['y'][ind] = (sentence_slice[1:]+next_letter)
        
    test_batch = batch_data(test_data[u], 32, 0)
    test_data_local_dict[client_num] = test_batch
    client_num += 1
        #print(len(test_data[u]['y'][ind]))
print(sentence_len)

80


In [6]:
print(NUM_LETTERS, client_num)

80 143


In [7]:
import torch
import torch.nn as nn

from ofa.utils.my_modules import MyConv2d

__all__ = ["profile"]


def count_convNd(m, _, y):
    cin = m.in_channels

    kernel_ops = m.weight.size()[2] * m.weight.size()[3]
    ops_per_element = kernel_ops
    output_elements = y.nelement()

    # cout x oW x oH
    total_ops = cin * output_elements * ops_per_element // m.groups
    m.total_ops = torch.zeros(1).fill_(total_ops)


def count_linear(m, _, __):
    total_ops = m.in_features * m.out_features

    m.total_ops = torch.zeros(1).fill_(total_ops)


register_hooks = {
    nn.Conv1d: count_convNd,
    nn.Conv2d: count_convNd,
    nn.Conv3d: count_convNd,
    MyConv2d: count_convNd,
    ######################################
    nn.Linear: count_linear,
    ######################################
    nn.Dropout: None,
    nn.Dropout2d: None,
    nn.Dropout3d: None,
    nn.BatchNorm2d: None,
}


def custom_profile(model, input_size, custom_ops=None):
    handler_collection = []
    custom_ops = {} if custom_ops is None else custom_ops

    def add_hooks(m_):
        if len(list(m_.children())) > 0:
            return

        m_.register_buffer("total_ops", torch.zeros(1))
        m_.register_buffer("total_params", torch.zeros(1))

        for p in m_.parameters():
            m_.total_params += torch.zeros(1).fill_(p.numel())

        m_type = type(m_)
        fn = None

        if m_type in custom_ops:
            fn = custom_ops[m_type]
        elif m_type in register_hooks:
            fn = register_hooks[m_type]

        if fn is not None:
            _handler = m_.register_forward_hook(fn)
            handler_collection.append(_handler)

    original_device = model.parameters().__next__().device
    training = model.training

    model.eval()
    model.apply(add_hooks)

    x = torch.zeros(input_size).to(original_device)
    x = x.to(torch.int32)
    with torch.no_grad():
        model(x)

    total_ops = 0
    total_params = 0
    for m in model.modules():
        if len(list(m.children())) > 0:  # skip for non-leaf module
            continue
        total_ops += m.total_ops
        total_params += m.total_params

    total_ops = total_ops.item()
    total_params = total_params.item()

    model.train(training).to(original_device)
    for handler in handler_collection:
        handler.remove()

    return total_ops, total_params

In [8]:
from fedml_api.standalone.flofa.elastic_nn.TCN.elastic_tcnn import (
    ElasticTCN
)
from torchsummary import summary

Supernet = ElasticTCN(input_size=450, output_size=80, num_channels=[450,450,450], kernel_size=3, depth_list=[0,1,2], expand_ratio_list=[0.2, 0.5, 1.0])
Supernet.set_max_net()
Maxnet = Supernet.get_active_subnet()
#print(Maxnet)
Supernet.set_active_subnet(d=0, e=0.2)
Minnet = Supernet.get_active_subnet()
Supernet.set_active_subnet(d=1, e=0.2)
small = Supernet.get_active_subnet()
Supernet.set_active_subnet(d=1, e=0.5)
middle = Supernet.get_active_subnet()
Supernet.set_active_subnet(d=1, e=1.0)
large = Supernet.get_active_subnet()
print(custom_profile(Maxnet, (32, 80)))
print(custom_profile(large, (32, 80)))

print(custom_profile(middle, (32, 80)))
print(custom_profile(small, (32, 80)))

print(custom_profile(Minnet, (32, 80)))



(36000.0, 3722480.0)
(36000.0, 2505680.0)
(36000.0, 1289780.0)
(36000.0, 560240.0)
(36000.0, 316160.0)


In [ ]:
for name, param in Supernet.named_parameters():
    print(name, param.shape)
for name, param in Maxnet.named_parameters():
    print(name, param.shape)

In [ ]:
##### saved_model_dict = torch.load("./best_checkpoint_supernet_1000.pt")
print(saved_model_dict.keys())
for item in saved_model_dict["params"]:
    print(item)
Supernet.load_state_dict(saved_model_dict["params"])

In [117]:
criterion = nn.CrossEntropyLoss()
Supernet.eval()
metrics = {"test_correct": 0, "test_loss": 0, "test_total": 0}
with torch.no_grad():
    ind = 0
    for u, g in zip(users, groups):
        total_loss = 0
        count = 0
        for batch_idx, (data, target) in enumerate(test_data_local_dict[ind]):
            #print(data, target)
            output = Supernet(data)

            # Discard the effective history, just like in training
            eff_history = data.size(1)-1
            final_output = output[:, eff_history:].contiguous().view(-1, 80)
            final_target = target[:, eff_history:].contiguous().view(-1)

            loss = criterion(final_output, final_target)

            #need to verify this
            _, predicted = torch.max(final_output, -1)
            #print(predicted, final_target)
            correct = predicted.eq(final_target).sum()
            metrics["test_correct"] += correct.item()
            metrics["test_total"] += final_target.size(0)
            # Note that we don't add TAR loss here
            total_loss += loss.data * final_output.size(0)
            count += final_output.size(0)
        print(metrics["test_correct"]/metrics["test_total"])
        metrics["test_loss"] = float(total_loss.item()) / count * 1.0
        ind+=1
    print("FINAL: ", metrics["test_correct"]/metrics["test_total"])

0.2066115702479339
0.21031746031746032
0.18762886597938144
0.18528995756718528
0.18097517200119653
0.1800219538968167
0.18337060378125636
0.18441660140955365
0.1841642228739003
0.18412822517591867
0.18402031646806016
0.18428135654046296
0.18438779553559637
0.1848937844217152
0.18509865005192108
0.1856566675069322
0.1859399831728522
0.18565751778948342
0.18666360786113023
0.18681650199864244
0.18690673497061924
0.1862708719851577
0.1859628514793334
0.18615226639284144
0.1861846447165799
0.18610785463071514
0.18536047717842324
0.18530066815144766
0.1859190031152648
0.18596120368067645
0.18574621306183264
0.18520089691533848
0.1851582833968888
0.185095586499882
0.18490090502921297
0.18495853588790392
0.18425004171069462
0.18465240361981483
0.1846604276676949
0.1845591594335313
0.1844582415381534
0.18403940886699507
0.1835609756097561
0.18340466000951022
0.18293922039534455
0.18284731026987863
0.18267631590776284
0.18279810358708293
0.1825123244004596
0.18222092044081573
0.1823152744801784

In [8]:
print(Maxnet(torch.tensor(x_batch)))

tensor([[[ 4.4712e-02, -3.4087e-02, -4.3675e-03,  ..., -6.0748e-02,
           5.5200e-02, -2.5832e-02],
         [ 1.4620e-02,  8.4335e-04,  2.9161e-03,  ...,  2.8897e-03,
           1.5503e-03,  1.2985e-03],
         [ 5.0265e-02, -7.0950e-03, -1.8549e-02,  ..., -3.2247e-02,
          -4.6709e-03,  2.5949e-02],
         ...,
         [ 4.8511e-02,  3.6070e-03,  4.5441e-03,  ..., -4.2880e-02,
          -9.9843e-03,  4.5156e-03],
         [ 7.6824e-02,  9.7441e-03, -4.6702e-02,  ..., -6.6686e-02,
           8.9336e-03,  2.9393e-03],
         [ 1.0143e-02, -2.7668e-05, -3.2032e-03,  ..., -4.7429e-02,
          -6.2955e-04, -2.5881e-03]],

        [[ 4.8577e-02, -4.8139e-02, -3.6598e-02,  ..., -4.4872e-02,
           3.5645e-02, -3.2387e-03],
         [ 2.3616e-02, -2.5027e-02, -3.4928e-02,  ..., -2.2043e-02,
           5.5759e-02, -2.4607e-02],
         [ 1.1222e-02, -3.0585e-02, -2.9698e-02,  ..., -2.2926e-02,
           1.3752e-02,  3.2531e-02],
         ...,
         [ 4.6909e-02, -1

In [34]:
print(users)
# user {
    x: x_1, x_2, x_3
    y: c_1, c_2
}

TCN
corpus
 " text "

['THE_TRAGEDY_OF_KING_LEAR_NYM', 'THE_TRAGEDY_OF_KING_LEAR_MOONSHINE', 'ALL_S_WELL_THAT_ENDS_WELL_ROMAN', 'THE_TAMING_OF_THE_SHREW_SERVANT', 'THE_FIRST_PART_OF_KING_HENRY_THE_FOURTH_FLUELLEN', 'THE_FIRST_PART_OF_KING_HENRY_THE_FOURTH_DAVY', 'THE_TRAGEDY_OF_KING_LEAR_MACDUFF', 'THE_TRAGEDY_OF_KING_LEAR_ANNE', 'THE_TAMING_OF_THE_SHREW_ALL_SERVANTS', 'THE_TRAGEDY_OF_KING_LEAR_DESERVING_A_FAIR_LADY', 'THE_TAMING_OF_THE_SHREW_TIMANDRA', 'THE_TRAGEDY_OF_KING_LEAR_KATHARINE', 'THE_TRAGEDY_OF_KING_LEAR_BOYET', 'ALL_S_WELL_THAT_ENDS_WELL_SECOND_GENTLEMAN', 'THE_TRAGEDY_OF_KING_LEAR_SECOND_MURTHERER', 'THE_TRAGEDY_OF_KING_LEAR_DULL', 'PERICLES__PRINCE_OF_TYRE_YORK', 'ALL_S_WELL_THAT_ENDS_WELL_HYMEN', 'ALL_S_WELL_THAT_ENDS_WELL_CELIA', 'THE_FIRST_PART_OF_KING_HENRY_THE_FOURTH_SIMPCOX', 'PERICLES__PRINCE_OF_TYRE_SECOND_MESSENGER', 'THE_TAMING_OF_THE_SHREW_SEMPRONIUS', 'THE_FIRST_PART_OF_KING_HENRY_THE_FOURTH_GRANDPRE', 'THE_FIRST_PART_OF_KING_HENRY_THE_FOURTH_THIRD_DRAWER', 'THE_TAMING_OF_THE_SHRE

In [40]:
#Train data
for u, g in zip(users, groups):
    #print("Group: ", g)
    #print("User: ", u)
    string_reconstruction = None
    prev_letter = None
    all_text_combine = None
    for sentence_slice, next_letter in zip(train_data[u]['x'], train_data[u]['y']):
        print(len(sentence_slice))
        if string_reconstruction is None:
            string_reconstruction = sentence_slice+next_letter
        else:
            i = len(sentence_slice)-1
            while(sentence_slice[i] != prev_letter and i >= 0):
                i-=1
            #if i < 0:
                #print(string_reconstruction)
                #print(sentence_slice)
                #print(next_letter, prev_letter)
            string_reconstruction += sentence_slice[i+1:]+next_letter
        prev_letter = next_letter
    if all_text_combine is None:
        all_text_combine = string_reconstruction
    else:
        all_text_combine += " " + string_reconstruction
    #print(string_reconstruction)
    #print("BREAK")

#Test data
'''for u, g in zip(users, groups):
    #print("Group: ", g)
    #print("User: ", u)
    string_reconstruction = None
    prev_letter = None
    all_text_combine = None
    for sentence_slice, next_letter in zip(test_data[u]['x'], test_data[u]['y']):
        if string_reconstruction is None:
            string_reconstruction = sentence_slice+next_letter
        else:
            i = len(sentence_slice)-1
            while(sentence_slice[i] != prev_letter and i >= 0):
                i-=1
            string_reconstruction += sentence_slice[i+1:]+next_letter
        prev_letter = next_letter
    if all_text_combine is None:
        all_text_combine = string_reconstruction
    else:
        all_text_combine += " " + string_reconstruction
#print(all_text_combine)'''

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

...

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
80
8

'for u, g in zip(users, groups):\n    #print("Group: ", g)\n    #print("User: ", u)\n    string_reconstruction = None\n    prev_letter = None\n    all_text_combine = None\n    for sentence_slice, next_letter in zip(test_data[u][\'x\'], test_data[u][\'y\']):\n        if string_reconstruction is None:\n            string_reconstruction = sentence_slice+next_letter\n        else:\n            i = len(sentence_slice)-1\n            while(sentence_slice[i] != prev_letter and i >= 0):\n                i-=1\n            string_reconstruction += sentence_slice[i+1:]+next_letter\n        prev_letter = next_letter\n    if all_text_combine is None:\n        all_text_combine = string_reconstruction\n    else:\n        all_text_combine += " " + string_reconstruction\n#print(all_text_combine)'

In [30]:
from collections import Counter

class Dictionary(object):
    def __init__(self):
        self.char2idx = {}
        self.idx2char = []
        self.counter = Counter()

    def add_word(self, char):
        self.counter[char] += 1

    def prep_dict(self):
        for char in self.counter:
            if char not in self.char2idx:
                self.idx2char.append(char)
                self.char2idx[char] = len(self.idx2char) - 1

    def __len__(self):
        return len(self.idx2char)


class Corpus(object):
    def __init__(self, string):
        self.dict = Dictionary()
        for c in string:
            self.dict.add_word(c)
        self.dict.prep_dict()

In [31]:
corpus = Corpus(all_text_combine)

In [ ]:
x:"n "
y:"m"

In [ ]:
x' = "[not the humour of bread and cheese; and there's the humour of it. Adieu. Exit Ny]"
y' = "[ot the ]humour of bread and cheese; and there's the humour of it. Adieu. Exit Nym"
model(x') = "[not the] humour of bread and cheese; and there's the humour of it. Adieu. Exit Ny"